In [41]:
%load_ext autoreload
%autoreload 2


import numpy as np
from utils.data_helper import *
from utils.data import *
from utils.stats import *
from utils.performance import *
from plotly.subplots import make_subplots
from account import Binance
import pandas as pd
import warnings
from strategy_v3.Strategy import *
from strategy_v3.Executor import ExecutorBinance, ExecutorBacktest
from strategy_v3.ExecuteSetup import *
from strategy_v3.DataLoader import DataLoaderBinance
from tqdm import tqdm
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
from time import sleep


pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 30)
warnings.filterwarnings('ignore')

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [223]:
symbol = 'BTCFDUSD'
binance = Binance()
df = binance.get_historical_instrument_price(symbol, interval='1m', start_str='2 hours ago')
plot_price_ohcl(df, symbol)
df['std'] = df['Close'].rolling(15).std()

# Market Making

In [323]:
spread_target
spread_target

0.010000000009313226

In [349]:
symbol = 'BTCUSDT'
df = binance.get_historical_instrument_price(symbol, interval='1m', start_str='2 hours ago')
df['std'] = df['Close'].rolling(15).std()
df['adv'] = df['Volume'].rolling(15).mean()
vol = df['std'].iloc[-1]
adv = df['adv'].iloc[-1]

df_bids, df_asks = Binance().get_order_book(instrument=symbol, limit=50)
spread_current = df_asks.iloc[0]['price'] - df_bids.iloc[0]['price']

flow_target = 0.03 * adv
spread_ask = df_asks[df_asks['quantity_cum'] > flow_target/2]['price'].min()
spread_bid = df_bids[df_bids['quantity_cum'] > flow_target/2]['price'].max()
spread_target = spread_ask - spread_bid

current_position = -0.0014*5
target_position = 0
vol = df['std'].iloc[-1] 
gamma = 0.05

mid_price = (df_asks.iloc[0]['price'] + df_bids.iloc[0]['price']) / 2
r = mid_price - (current_position - target_position) * gamma * vol ** 2
bid = r - spread_target/2
ask = r + spread_target/2


fig = make_subplots()
fig.update_layout(title=f'{symbol} (current spread = {spread_current:.4f}, target spread = {spread_target:.4f}, adv = {adv:.4f})', width=800, height=500, hovermode='x')
fig.add_trace(go.Scatter(x=df_bids['price'], y=df_bids['quantity_cum'], name='bid'))
fig.add_trace(go.Scatter(x=df_asks['price'], y=df_asks['quantity_cum'], name='ask'))
fig.add_vline(bid, line_dash="dash", line_color="blue")
fig.add_vline(ask, line_dash="dash", line_color="red")
fig.show()

In [350]:
strategy = SimpleMarketMakingStrategy(
    instrument = 'BTCFDUSD',
    interval = '1m',
    vol_lookback = 20,                      
    spread_adv_factor=0.05,    
    target_position = 0,                
    position_size = 100,
    price_decimal = 2,
    qty_decimal = 4,                             
    status = STATUS.RUN,
    verbose = True,       
    start_date = '2024-03-12 16:00:00'
)
strategy.set_data_loder(DataLoaderBinance())
strategy.set_executor(ExecutorBinance())
strategy.set_strategy_id('SMM_BTCv4')    

In [352]:
strategy.load_data('')
strategy.summary()


Measure  smm_SMM_BTCv4
0                      Pnl     -18.605110
1              Trading Fee       0.000000
2        Cumulative Return       0.906974
3        Annualized Return      -8.122696
4    Annualized Volatility       0.421303
5  Annualized Sharpe Ratio     -19.399368
6         Maximum Drawdown      -0.097839